In [6]:
import pandas as pd
import numpy as np

import string
import random
import requests

from itertools import groupby
from tqdm import tqdm
import re

import plotly.graph_objects as go
import plotly
import plotly.express as px
import sklearn
from sklearn.metrics import recall_score, precision_score
from sklearn.metrics import roc_curve, auc, f1_score

In [2]:
iter_list = ['numbers']         
iter_list.extend(list(string.ascii_lowercase))

for end in iter_list:
    if end == "numbers":
        table_start = pd.read_html(f"http://pfam-legacy.xfam.org/family/browse?browse={end}", header = 1)[0]
    else:
        table = pd.read_html(f"http://pfam-legacy.xfam.org/family/browse?browse={end}", header = 1)[0]
        table_start = pd.concat([table_start, table])
    


In [3]:
table_final = table_start[(table_start.Type == "Domain") & (table_start.Full <= 900) & (table_start.Full >= 100) &(table_start['Average length'] <= 150)&(table_start['Average %id'] >= 30)]          #Некоторые ограничения на поиск...
table_final

ID Accession    Type  Seed  Full  Average length  Average %id  \
14        2C_adapt   PF08793  Domain    18   141            34.7           40   
42       3HCDH_RFF   PF18321  Domain    24   551            67.4           39   
47             4HB   PF17947  Domain    90   556            77.1           41   
58    53-BP1_Tudor   PF09038  Domain     2   604           118.2           69   
2    A2L_zn_ribbon   PF08792  Domain    12   100            31.5           32   
..             ...       ...     ...   ...   ...             ...          ...   
201  zinc_ribbon_5   PF13719  Domain     3   624            36.7           50   
213    ZNRF_3_ecto   PF18212  Domain     5   722            94.6           55   
221    Zn_ribbon_2   PF12674  Domain    90   703            78.5           35   
224     Zn_Tnp_IS1   PF03811  Domain     3   521            32.0           38   
228    ZoocinA_TRD   PF16775  Domain     4   181            79.3           51   

     Average coverage  Has 3D Change status  \
14              17.40     NaN       Changed   
42              13.28     NaN       Changed   
47               7.40     NaN       Changed   
58               7.25     NaN       Changed   
2               13.60     NaN       Changed   
..                ...     ...           ...   
201              9.17     NaN       Changed   
213             13.03     NaN       Changed   
221             58.16     NaN       Changed   
224             25.42     NaN       Changed   
228             37.00     NaN       Changed   

                                           Description  
14                           2-cysteine adaptor domain  
42   3-hydroxybutyryl-CoA dehydrogenase reduced Ros...  
47                          Four helical bundle domain  
58       Tumour suppressor p53-binding protein-1 Tudor  
2                               A2L zinc ribbon domain  
..                                                 ...  
201                                 zinc-ribbon domain  
213                                  ZNRF-3 Ectodomain  
221                        Putative zinc ribbon domain  
224                             InsA N-terminal domain  
228       Target recognition domain of lytic exoenzyme  

[966 rows x 11 columns]

In [7]:
list_bool = []
for ac in tqdm(list(table_final.Accession)):
    url = f"http://pfam-legacy.xfam.org/family/{ac}" 
    num_arch = re.findall(r"([\d]+)[\D]+?architecture", requests.get(url).text)[0]                                   #Попытка контролировать также количество архитектур... Получилось, но очень странно. Работает ооочень долго. 
    if (int(num_arch) == 3 or int(num_arch == 4)):
        list_bool.append(True)
    else:
        list_bool.append(False)

100%|█████████████████████████████████████████| 966/966 [16:04<00:00,  1.00it/s]


In [8]:
random.choices(list(table_final.loc[np.array(list_bool), :].Accession), k=10)                          #Брал рандомные выборки и далее проверял глазами, подходят ли мне архитектуры или нет. 

['PF15616',
 'PF15289',
 'PF08792',
 'PF12647',
 'PF19802',
 'PF19294',
 'PF19837',
 'PF18282',
 'PF11703',
 'PF09164']

In [9]:
with open("FN3_7_full-220.fasta", "r") as file:
    AC_all = filter(lambda x: x.startswith(">"), file.readlines())
    AC_all = np.array(list(map(lambda x: x.split()[0][1:], AC_all)))                 #AC всех последовательностей в full-выборке.
    
with open("AC", "r") as file:
    AC_arc = list(map(lambda x: x.split()[0], file.readlines()))                     #AC белков, включающух выбранную архитектуру.

In [29]:
with open('arc_aligned2.fasta', 'r') as file:
    text = list(map(lambda x: x.split('/')[0][1:], filter(lambda x: x.startswith('>'), file.readlines())))

list_bool3 = []
list_bool2 = []
for ac_all in AC_all:
    if ac_all in AC_arc:
        list_bool2.append([ac_all, True])
    else:
        list_bool2.append([ac_all, False])
        
    if ac_all in text:
        list_bool3.append([ac_all, True])
    else:
        list_bool3.append([ac_all, False])
        
list_bool2 = np.array(list_bool2)
list_bool3 = np.array(list_bool3)                              #Просто для того, чтобы удобно было создать нужные булевые колонки в табличке Pandas.

In [11]:
AC_table = pd.DataFrame(list_bool2, columns = ['AC', 'Belonging to architecture'])
AC_table2 = pd.DataFrame(list_bool3, columns = ['AC', 'Belonging to alignment for HMM'])

In [12]:
with open("FN3_7_full-120.fasta", "r") as file:
    text = file.readlines()

dic = dict()
for header, seq in groupby(text, key=lambda x: x.startswith(">")):
    if header:
        name = next(seq).split()[0][1:]
    else:
        seq = ''.join(map(lambda x: x.rstrip(), seq))                                          
    dic[name] = seq                                                          #Словарь: AC последовательности   ->  последовательность.
             
with open('arc.fasta', 'w') as file:
    for name in AC_table[AC_table['Belonging to architecture'] == 'True'].AC.values:
        print(f'>{name}', dic[name], file=file, sep='\n', end='')                                #Создание fasta-файля (для последующего выравнивания) нужных последовательностей.
               
with open('Table_scores', 'r') as file:                                                        #Та самая таблица, полученная в результате работы HMMsearch. Пришлось руками её копировать. 
    text = file.readlines()        

with open('Table_scores.tsv', 'w') as file:
    print(*map(lambda x: re.sub(r"[\s]{2,}", '\t', x).rstrip(), text), file=file, sep='\n')                      #Таблица ужасная, куча пробелов не по делу. Pandas в шоке. Пришлось удалять тем, что под руку попалось...
    
Table_scores = pd.read_csv('Table_scores.tsv', names = ['AC', "Domain", "seq-f", "seq-t", "hmm-f", "hmm-t", "score", "E-value"], dtype = {'score': float}, sep='\t')              #Ну, наконец...

Table_scores = pd.merge(pd.merge(AC_table, AC_table2), Table_scores)                               #Объединяю, чтобы в таблице были те самые нужные булевые столбцы. 
Table_scores.drop(columns=['Domain', 'seq-f', 'hmm-f', 'seq-t', 'hmm-t'], inplace=True)                                                #Удаляю ненужности.
 
Table_scores['Belonging to architecture'] = Table_scores['Belonging to architecture'].apply(lambda x: True if x == 'True' else False)                           #Сделал True и False булевыми, а не строками в колонке (просто надо было).
Table_scores.sort_values(by=['score'], ascending=False, inplace=True)

sensitivity = [0, ]
for it in range(1, len(Table_scores) + 1):                              
    sensitivity.append(Table_scores.iloc[:it, 1].value_counts()[True] / Table_scores['Belonging to architecture'].value_counts()[True])                       #Sensitivity руками.
    
alpha = [0, ]              
for it in range(1, len(Table_scores) + 1):
    alpha.append((Table_scores.iloc[:it, 1].value_counts()[False] if False in Table_scores.iloc[:it, 1].value_counts() else 0)/(Table_scores['Belonging to architecture'].value_counts()[False]))      # 1 - Specificity руками.
    
fpr, tpr, thresholds = roc_curve(Table_scores['Belonging to architecture'].astype(int), Table_scores.score)                         # ROC-curve не руками. Sklearn.   (Sens. и 1 - Spec. не руками)

f1_sc = []
for it in range(1, len(Table_scores) + 1):
    f1_sc.append(f1_score(Table_scores['Belonging to architecture'].astype(int), [1] * it + [0] * (len(Table_scores) - it)))                   #F1-score не руками. 
    
Table_scores = Table_scores.reset_index(col_level=0).drop(columns=['index'])
Table_scores.insert(value = np.array(sensitivity[1:]), loc = 5, column = 'Sensitivity')
Table_scores.insert(value = np.array(alpha[1:]), loc = 6, column = '1 - Specificity')
Table_scores.insert(value = np.array(f1_sc), loc = 7, column = 'F1-score')                               #Приведение таблицы в порядок, если это вообще так назвать можно...

In [46]:
Table_scores.sort_values(by = ['F1-score'], ascending= False)                             #Вот такая она... Здесь на первом месте максимальный F1-score -> вес, соответствующий значению, можно считать за пороговый. 

AC  Belonging to architecture  \
139  A0A2K5TPW0_MACFA                       True   
140  A0A4D9EK02_9SAUR                      False   
138      F7G3H6_MACMU                       True   
141  A0A663FEI4_AQUCH                      False   
137  A0A671F7I8_RHIFE                       True   
..                ...                        ...   
4    A0A341C786_NEOAA                       True   
3        F7DGM3_HORSE                       True   
2         IL7RA_HORSE                       True   
1    A0A6I9HZM6_VICPA                       True   
0    A0A5N4EDY1_CAMDR                       True   

    Belonging to alignment for HMM   score       E-value  Sensitivity  \
139                          False   159.0  2.900000e-46     1.000000   
140                          False   122.9  2.300000e-35     1.000000   
138                          False   159.0  2.900000e-46     0.990196   
141                          False   106.8  1.500000e-30     1.000000   
137                          False   169.0  3.000000e-49     0.980392   
..                             ...     ...           ...          ...   
4                             True  1088.2  0.000000e+00     0.049020   
3                             True  1091.5  0.000000e+00     0.039216   
2                            False  1092.0  0.000000e+00     0.029412   
1                            False  1101.7  0.000000e+00     0.019608   
0                             True  1103.1  0.000000e+00     0.009804   

     1 - Specificity  F1-score  
139         0.324786  0.842975  
140         0.333333  0.839506  
138         0.324786  0.838174  
141         0.341880  0.836066  
137         0.324786  0.833333  
..               ...       ...  
4           0.000000  0.093458  
3           0.000000  0.075472  
2           0.000000  0.057143  
1           0.000000  0.038462  
0           0.000000  0.019417  

[219 rows x 8 columns]

In [52]:
import plotly.io as pio
pio.renderers.default = 'iframe'

y1 = [605.3, 605.3]
y1.extend(Table_scores.score[99:])
x1 = [0, 98]
x1.extend(range(99, 219))

y2 = [159, 159]
y2.extend(Table_scores.score[140:])
x2 = [0, 139]
x2.extend(range(140, 219))

fig = go.Figure()
fig.add_trace(go.Scatter(y=Table_scores.score,
    fill=None,
    mode='lines',
    line_color='LightSkyBlue',
    ))
fig.add_trace(go.Scatter(y=y1,
    x=x1,
    fill='tonexty',
    mode='lines',
    line_color='LightSkyBlue',
    ))
fig.add_trace(go.Scatter(y=y2,
    x=x2,
    fill='tonexty',
    mode='lines',
    line_color='LightGreen',
    ))
fig.add_trace(go.Scatter(
    y=[-282.8],
    fill='tonexty', # fill area between trace0 and trace1
    mode='lines', line_color='Red'))
fig.update_layout(margin=dict(l=50, r=50, t=50, b=50),
                  width=1500,
                  height=800,
                  showlegend=False,
                  yaxis_title="Score",
                  hovermode="x",
                  paper_bgcolor="#e5ffff",
                  font=dict(
                    family="Courier New, monospace",
                    size=14,
                    color="Black"),
                  title=dict(text="Decrease of score", font=dict(size=40), automargin=True, yref='paper', y = 0.5, x = 0.5, yanchor = 'auto'),
                  title_font_family="Times New Roman")
fig.update_traces(hoverinfo="y", hovertemplate="Вес %{x}-ой последовательности: %{y}")
fig.update_yaxes(range=[-200, 1130])

fig.show()

In [54]:
fig = px.histogram(data_frame=Table_scores, x='score', color='Belonging to architecture',
             width=1500, height=1000, pattern_shape="Belonging to architecture", 
                  color_discrete_sequence=px.colors.qualitative.Pastel)
fig.update_layout(yaxis_title="Count",
                  xaxis_title="Score",
                  hovermode="x",
                  paper_bgcolor="#e5ffff",
                  font=dict(
                    family="Courier New, monospace",
                    size=14,
                    color="Black"),
                  title=dict(text="Score histogram ", font=dict(size=40), automargin=True, yref='paper', y = 0.5, x = 0.28, yanchor = 'auto', xanchor='left'),
                  title_font_family="Times New Roman")
fig.show()


In [55]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=fpr, y=tpr, mode="lines", name="ROC curve", line=dict(color = 'Blue')))
fig.add_trace(go.Scatter(x=[0, 1], y=[0, 1], mode="lines", line=dict(color = 'Black', dash='dash')))

fig.update_layout(margin=dict(t=50,
                              r=50,
                              l=50,
                              b=50),
                  legend=dict(x=0.5, xanchor="center"),
                  xaxis_title="False Positive Rate, %",
                  yaxis_title="Sensitivity",
                  hovermode="x", 
                  paper_bgcolor='#e5ffff', width=1500, height=1000, font=dict(
                    family="Courier New, monospace",
                    size=14,
                    color="Black"),
                  title=dict(text="ROC curve", font=dict(size=40), automargin=True, yref='paper', y = 0.5, x = 0.5, yanchor = 'auto'),
                  title_font_family="Times New Roman",
                  showlegend=False)
fig.update_traces(hoverinfo="all", hovertemplate="True Positive Rate: %{y} <br> False Positive Rate: %{y}")
fig.update_yaxes(range=[0, 1.05])
fig.show()

In [17]:
print(f'Площадь под кривой (AUC) равна: {auc(fpr, tpr)}')

Площадь под кривой (AUC) равна: 0.8589324618736383


In [18]:
lengths = list(map(lambda x: len(x), dic.values()))
lengths = pd.DataFrame(lengths, columns=['Length'])

In [44]:
fig = px.histogram(data_frame=lengths, x='Length',
             width=1800, height=1000, 
                  color_discrete_sequence=px.colors.qualitative.Pastel2)
fig.update_layout(yaxis_title="Count",
                  xaxis_title="Length",
                  hovermode="x",
                  paper_bgcolor="#e5ffff",
                  title=dict(text="Length histogram", font=dict(size=40), automargin=True, yref='paper', y = 0.5, x = 0.5, yanchor = 'auto'),
                  )

fig.update_xaxes(tickvals = [100, 200, 300, 400, 500, 700, 1900, 2000, 2300])
